In [36]:
import importlib
import sys
import os
    
def getImporter():
    nixSuite=os.path.join(os.path.expanduser('~'),'software','src','nixSuite')
    sys.path.append(os.path.join(nixSuite,'wrapper'))
    import nixWrapper
    nixWrapper.loadLibrary('labkeyInterface')
    import importXLSX
    importlib.reload(importXLSX)
    return importXLSX

def modify(qv,columnName):
    if columnName=='ROBOVI - najbližji':
        qv=qv.replace('mm','')
        qv=qv.replace(',','.')
    return qv

def modifyRT(qv,columnName):
    pMap={'obsevano področje':parseRTArea,
         'Boost':parseX,
          'tehnika obsevanja':parseRTTechnique,
          'tehnika boosta':parseBoostTechnique,
          'obsevanje v globokem vdihu':parseX
         }
    for p in pMap:
        if columnName==p:
            qv=pMap[p](qv)
    return qv  

def parseMap(qv,vmap):
    for v in vmap:
        if qv==v:
            return vmap[v]
    return qv

def parseRTArea(qv):
    vmap={'3 (cela dojka + lezija)':3, 
          '3 - cela dojka + ležišče':3,
          '3 - leva dojka in ležišče':3,
          'X':None
         }
    return parseMap(qv,vmap)
    
def parseX(qv):
    vmap={'X':None}
    return parseMap(qv,vmap)


def parseRTTechnique(qv):
    vmap={'3D fif':4,
          '3 - ABC':5,
          '3 - 3D + E boost':6,
          '3 - ABC, 3D-CRT':7,
          '3D fif - ABC, SIB':8,
          '3D fif - ABC':10,
          'DIBH 3D + FREE 3D fif':11,
          'X':None}
          
    return parseMap(qv,vmap)
    
def parseBoostTechnique(qv):
    vmap={'X':None,
         'elekt.':2,
         'e boost':2}
          
    return parseMap(qv,vmap)
    

def getGlobalId(df,r):
    possibleLabels=['ID','zaporedna št v raziskavi','ID študija']
    rawId=None
    for x in possibleLabels:
        try:
            rawId=str(df.at[r,x])
        except KeyError:
            continue
    #drop spaces
    rawId=rawId.replace(' ','')
    #print(rawId)
    return rawId

def convertLookup(xlsColumnName):
    return False


    
 

In [38]:
importXLSX=getImporter()
filename=os.path.join('z:','DCIS_import1.xlsx')
filename1=os.path.join('z:','DCISimportRT.xlsx')
#print(os.path.isfile(filename))

#Demographics
parServer={'server':'onko-nix',
      'project':'DCIS/Study',
      'schema':'study'}

parXLS= {'sheet_name':0,  'skiprows':6}
parXLS1= {'sheet_name':1,  'skiprows':0}
parXLS2= {'sheet_name':0,  'skiprows':0}

#DEMOGRAPHICS
parD={'query':'Demographics'}

##PART 1
#importData(parServer| parD | parXLS,filename,getGlobalId,dryRun=True)

#PART 2
#importData(parServer| parD | parXLS1,filename,getGlobalId,dryRun=False)

#COMORBIDITIES
parC={'query':'comorbidities'}
#importData(parServer | parC | parXLS,filename,getGlobalId,dryRun=True)

#TOXICITY
parT={'query':'toxicity'}

## VISIT 1
parTV1={'usecols':'A,O:AG', 'seqNumOffset':0}
#importData(parServer | parT | parXLS | parTV1,filename,getGlobalId,dryRun=True)

## VISIT 2
parTV2={'usecols':'A,AH:AZ', 'seqNumOffset':1}
#importData(parServer | parT | parXLS | parTV2,filename,getGlobalId,dryRun=True)

## VISIT 3
parTV3={'usecols':'A,BA:BP', 'seqNumOffset':2}
#importData(parServer | parT | parXLS | parTV3,filename,getGlobalId,dryRun=True)

## VISIT 4
parTV4={'usecols':'A,BQ:CF', 'seqNumOffset':3}
#importData(parServer | parT | parXLS | parTV4,filename,getGlobalId,dryRun=True)

## VISIT 5
parTV5={'usecols':'A,CG:CW', 'seqNumOffset':4}
#importData(parServer | parT | parXLS | parTV5,filename,getGlobalId,dryRun=True)

# CANCER DATA
parCA={'query':'cancerData'}
#importData(parServer | parCA | parXLS1,filename,getGlobalId,dryRun=True)

#SURGERY
parSG={'query':'surgery'}
#importData(parServer | parSG | parXLS1,filename,getGlobalId,dryRun=True)

#RT
parRT={'query':'radiotherapy'}
#importData(parServer | parRT | parXLS1,filename,getGlobalId,dryRun=True)
importXLSX.importData(parServer | parRT | parXLS2,filename1,getId=getGlobalId,
                      modify=modifyRT,
                      convertLookup=convertLookup,
                      dryRun=False,
                      debug=False)

#laboratoryTests
parLT={'query':'laboratoryTests'}
## VISIT 1
parLTV1={'usecols':'A,AO,AS,AW', 'seqNumOffset':1}
#importData(parServer | parLT | parXLS1 | parLTV1,filename,getGlobalId,dryRun=False)

## VISIT 2
parLTV2={'usecols':'A,AP,AT,AX', 'seqNumOffset':2}
#importData(parServer | parLT | parXLS1 | parLTV2,filename,getGlobalId,dryRun=False)

## VISIT 3
parLTV3={'usecols':'A,AQ,AU,AY', 'seqNumOffset':3}
#importData(parServer | parLT | parXLS1 | parLTV3,filename,getGlobalId,dryRun=False)


## VISIT 4
parLTV4={'usecols':'A,AR,AV,AZ', 'seqNumOffset':4}
#importXLSX.importData(parServer | parLT | parXLS1 | parLTV4,filename,getGlobalId,modify,convertLookup,dryRun=True)

## IMAGING1
parIm={'query':'Imaging1','usecols':'A,C'}
#importXLSX.importData(parServer | parIm | parXLS2 ,filename1,getGlobalId,modify,convertLookup,dryRun=False,debug=False)


#df=pandas.read_excel(filename,skiprows=6,usecols=parsT5['usecols'])
#print(df)

#for repeated evaluations, apply columnt offset (or selection) and provide seqNumOffset


loadLibrary
remoteSourcesURL https://git0.fmf.uni-lj.si/studen/nixSuite/raw/master/remoteResources/resources.json
{'labkeyInterface': {'url': 'https://git0.fmf.uni-lj.si/studen/labkeyInterface/archive/master.zip', 'branch': 'master', 'modules': []}, 'irAEMM': {'url': 'https://git0.fmf.uni-lj.si/studen/iraemm/archive/master.zip', 'branch': 'master', 'modules': ['iraemmBrowser']}, 'SlicerLabkeyExtension': {'url': 'https://git0.fmf.uni-lj.si/studen/SlicerLabkeyExtension/archive/SlicerExtensionIndex.zip', 'branch': 'SlicerExtensionIndex', 'modules': ['labkeyBrowser']}, 'limfomiPET': {'url': 'https://git0.fmf.uni-lj.si/studen/limfomiPET/archive/master.zip', 'branch': 'master', 'modules': ['imageBrowser', 'segmentationBrowser']}, 'parseConfig': {'url': 'https://git0.fmf.uni-lj.si/studen/parseConfig/archive/master.zip', 'branch': 'master', 'modules': []}, 'orthancInterface': {'url': 'https://git0.fmf.uni-lj.si/studen/orthancInterface/archive/master.zip', 'branch': 'master', 'modules': []}, 'd